# 使用 Transformers 处理音频


在本笔记中，我们将使用 Hugging Face 的 Transformers 库来处理音频数据。


## 零样本分类


我们从计算机视觉中已知的问题开始：零样本分类。该任务是指在没有针对特定类别进行训练的情况下，确定一段音频的来源。


### 实现步骤


为此，我们使用 ESC-50 数据集（ashraq/esc50），该数据集包含分为 50 个不同类别的 5 秒音频录音。
我们可以使用 Hugging Face 的 datasets 库来下载该数据集：


In [1]:
from datasets import load_dataset
from transformers import pipeline
from IPython.display import Audio as IPythonAudio

/home/aquilae/anaconda3/envs/dev/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [ ]:
dataset = load_dataset("ashraq/esc50",split="train[0:10]")

我们可以查看音频片段的元数据。*采样率（sampling_rate）* 尤为重要，必须确保其与模型训练数据的采样率一致。


In [6]:
audio_sample = dataset[0]
audio_sample

{'filename': '1-100038-A-14.wav',
 'fold': 1,
 'target': 14,
 'category': 'chirping_birds',
 'esc10': False,
 'src_file': 100038,
 'take': 'A',
 'audio': {'path': None,
  'array': array([-0.01184082, -0.10336304, -0.14141846, ...,  0.06985474,
          0.04049683,  0.00274658]),
  'sampling_rate': 44100}}

我们可以使用 IPython 来播放音频片段（注意不要将电脑音量调得太大）。


In [7]:
IPythonAudio(audio_sample["audio"]["array"],rate=audio_sample["audio"]["sampling_rate"])

现在，我们将使用 Hugging Face 的 pipeline 来加载模型。
我们使用的是 LAION-AI 的 CLAP 模型（laion/clap-htsat-unfused）。


In [9]:
audio_zero_shot = pipeline(task="zero-shot-audio-classification",model="laion/clap-htsat-unfused")

我们需要查看模型的 *采样率*，以确认其是否与我们的数据采样率匹配。


In [14]:
print("Sampling rate du modèle : ",audio_zero_shot.feature_extractor.sampling_rate)
print("Sampling rate de notre extrait : ",audio_sample["audio"]["sampling_rate"])

Sampling rate du modèle :  48000
Sampling rate de notre extrait :  44100


我们需要调整数据集的 *采样率*，以适应模型的要求。


In [16]:
from datasets import Audio
dataset = dataset.cast_column("audio",Audio(sampling_rate=48_000))
audio_sample = dataset[0]
print("Sampling rate de notre extrait : ",audio_sample["audio"]["sampling_rate"])

Sampling rate de notre extrait :  48000


现在音频片段和模型的采样率已同步，我们可以进行分类。
我们将提供一些候选标签（类似于视觉中的 CLIP 模型）。


In [18]:
candidate_labels = ["Sound of a dog","Sound of cat"]
outputs=audio_zero_shot(audio_sample["audio"]["array"],candidate_labels=candidate_labels)
print("Score de "+candidate_labels[0],outputs[0]["score"])
print("Score de "+candidate_labels[1],outputs[1]["score"])

Score de Sound of a dog 0.9805886149406433
Score de Sound of cat 0.019411340355873108


模型能够识别出该音频片段是狗叫声，而不是猫叫声。
您可以使用自己的音频片段或数据集中的其他片段进行测试。


## 自动语音识别


自动语音识别是将语音转录为文本的过程。该技术可用于语音笔记记录、激活智能设备（如“Ok Google”、“Hey Siri”）等多种应用场景。


### 实现步骤


在本示例中，我们使用 LibriSpeech ASR 语料库，该语料库包含约 1000 小时的英语语音数据。


In [19]:
from datasets import load_dataset
dataset = load_dataset("librispeech_asr",split="train.clean.100",streaming=True,trust_remote_code=True)

In [25]:
example = next(iter(dataset))
example

{'file': '374-180298-0000.flac',
 'audio': {'path': '374-180298-0000.flac',
  'array': array([ 7.01904297e-04,  7.32421875e-04,  7.32421875e-04, ...,
         -2.74658203e-04, -1.83105469e-04, -3.05175781e-05]),
  'sampling_rate': 16000},
 'text': 'CHAPTER SIXTEEN I MIGHT HAVE TOLD YOU OF THE BEGINNING OF THIS LIAISON IN A FEW LINES BUT I WANTED YOU TO SEE EVERY STEP BY WHICH WE CAME I TO AGREE TO WHATEVER MARGUERITE WISHED',
 'speaker_id': 374,
 'chapter_id': 180298,
 'id': '374-180298-0000'}

In [24]:
from IPython.display import Audio as IPythonAudio

IPythonAudio(example["audio"]["array"],rate=example["audio"]["sampling_rate"])

我们将使用 OpenAI 的 Whisper 模型（distil-whisper/distil-small.en），该模型专为英语语音识别而设计，是原始模型的精简版本。
现在，我们构建 Hugging Face 的 pipeline。


In [27]:
reco_parole = pipeline(task="automatic-speech-recognition",model="distil-whisper/distil-small.en")

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [30]:
print("Sampling rate du modèle : ",reco_parole.feature_extractor.sampling_rate)
print("Sampling rate de notre extrait : ",example['audio']['sampling_rate'])

Sampling rate du modèle :  16000
Sampling rate de notre extrait :  16000


由于 *采样率* 一致，因此无需进行任何调整。


In [37]:
output=reco_parole(example["audio"]["array"])
print("Texte transcrit : ",output['text'])
print("Texte de base : ",example["text"].lower())

Texte transcrit :   Chapter 16 I might have told you of the beginning of this liaison in a few lines, but I wanted you to see every step by which we came. I too agree to whatever Marguerite wished.
Texte de base :  chapter sixteen i might have told you of the beginning of this liaison in a few lines but i wanted you to see every step by which we came i to agree to whatever marguerite wished


如您所见，转录结果与原始音频非常吻合。


## 文本到语音转换


该任务与之前的任务相反。在这里，我们输入文本，模型会生成一个人朗读该文本的音频。


### 实现步骤


我们使用 kakao-enterprise 的 vits 模型（kakao-enterprise/vits-ljs）。


In [5]:
text_parole = pipeline("text-to-speech", model="kakao-enterprise/vits-ljs")

Some weights of the model checkpoint at kakao-enterprise/vits-ljs were not used when initializing VitsModel: ['flow.flows.0.wavenet.in_layers.0.weight_g', 'flow.flows.0.wavenet.in_layers.0.weight_v', 'flow.flows.0.wavenet.in_layers.1.weight_g', 'flow.flows.0.wavenet.in_layers.1.weight_v', 'flow.flows.0.wavenet.in_layers.2.weight_g', 'flow.flows.0.wavenet.in_layers.2.weight_v', 'flow.flows.0.wavenet.in_layers.3.weight_g', 'flow.flows.0.wavenet.in_layers.3.weight_v', 'flow.flows.0.wavenet.res_skip_layers.0.weight_g', 'flow.flows.0.wavenet.res_skip_layers.0.weight_v', 'flow.flows.0.wavenet.res_skip_layers.1.weight_g', 'flow.flows.0.wavenet.res_skip_layers.1.weight_v', 'flow.flows.0.wavenet.res_skip_layers.2.weight_g', 'flow.flows.0.wavenet.res_skip_layers.2.weight_v', 'flow.flows.0.wavenet.res_skip_layers.3.weight_g', 'flow.flows.0.wavenet.res_skip_layers.3.weight_v', 'flow.flows.1.wavenet.in_layers.0.weight_g', 'flow.flows.1.wavenet.in_layers.0.weight_v', 'flow.flows.1.wavenet.in_layers.

我们尝试生成一句法语。


In [6]:
text = """Ce cours de deep learning est incroyable."""
generated_parole = text_parole(text)
IPythonAudio(generated_parole["audio"][0],rate=generated_parole["sampling_rate"])

如您所见，结果不太理想，因为该模型是基于英语数据训练的。如果您想生成法语音频，需要寻找适合的模型。
现在我们尝试用一句英语：


In [7]:
text = """This deep learning course is fantastic."""
generated_parole = text_parole(text)
IPythonAudio(generated_parole["audio"][0],rate=generated_parole["sampling_rate"])

效果好多了！


**注意 1**：您也可以组合多个模型。例如，将法语句子翻译成英语，再生成对应的音频。

**注意 2**：如果您希望生成非语音的音频（如音乐、环境音、噪音等），则应查看 Hugging Face 上的“文本到音频（Text-to-Audio）”类别。
